<a href="https://colab.research.google.com/github/kasprova/CV_UCU/blob/master/module5/practice/cv_module5_task3_test_efficientnet_cifar10.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Link to colab: https://colab.research.google.com/drive/1BnRQ7mStr0VLHDPfe9yxtaryDwOWAb2x

In [0]:
# [colab version] latest version of tensorflow in order to use tensorboard inside the notebook
!pip install -q tf-nightly-2.0-preview #tensorflow build

In [0]:
import numpy as np
import matplotlib.pyplot as plt

import datetime

import torch
import torchvision
import torchvision.transforms as transforms

import tensorflow as tf

# for tensorboard
from torch.utils.tensorboard import SummaryWriter

In [0]:
# random seed settings
torch.manual_seed(42)
np.random.seed(42)


In [34]:
# Load the TensorBoard notebook extension
%load_ext tensorboard

# for auto-reloading external modules (files, etc.)
%load_ext autoreload
%autoreload 2

# to be able to make plots inline the notebook 
# (actually no need for the colab version)
%matplotlib inline

# make plots a bit nicer
plt.matplotlib.rcParams.update({'font.size': 18, 'font.family': 'serif'})

The tensorboard extension is already loaded. To reload it, use:
  %reload_ext tensorboard
The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [0]:
# path for dataset (will be not there after end of session)
path_data = "./data"

In [0]:
no_cuda = False
use_cuda = not no_cuda and torch.cuda.is_available()
device = torch.device("cuda" if use_cuda else "cpu")

In [37]:
device

device(type='cuda')

In [38]:
transform = transforms.Compose(
    [transforms.ToTensor(),
     transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))])

trainset = torchvision.datasets.CIFAR10(root=path_data, train=True,
                                        download=True, transform=transform)
trainloader = torch.utils.data.DataLoader(trainset, batch_size=32,
                                          shuffle=True, num_workers=2)

testset = torchvision.datasets.CIFAR10(root=path_data, train=False,
                                       download=True, transform=transform)
testloader = torch.utils.data.DataLoader(testset, batch_size=32,
                                         shuffle=False, num_workers=2)

classes = ('plane', 'car', 'bird', 'cat',
           'deer', 'dog', 'frog', 'horse', 'ship', 'truck')


Files already downloaded and verified
Files already downloaded and verified


In [39]:
ls data

cifar-10-batches-py/  cifar-10-python.tar.gz


In [0]:
import torch
import torch.nn as nn
import torch.nn.functional as F


class Block(nn.Module):
    '''expand + depthwise + pointwise + squeeze-excitation'''

    def __init__(self, in_planes, out_planes, expansion, stride):
        super(Block, self).__init__()
        self.stride = stride

        planes = expansion * in_planes
        self.conv1 = nn.Conv2d(
            in_planes, planes, kernel_size=1, stride=1, padding=0, bias=False)
        self.bn1 = nn.BatchNorm2d(planes)
        self.conv2 = nn.Conv2d(planes, planes, kernel_size=3,
                               stride=stride, padding=1, groups=planes, bias=False)
        self.bn2 = nn.BatchNorm2d(planes)
        self.conv3 = nn.Conv2d(
            planes, out_planes, kernel_size=1, stride=1, padding=0, bias=False)
        self.bn3 = nn.BatchNorm2d(out_planes)

        self.shortcut = nn.Sequential()
        if stride == 1 and in_planes != out_planes:
            self.shortcut = nn.Sequential(
                nn.Conv2d(in_planes, out_planes, kernel_size=1,
                          stride=1, padding=0, bias=False),
                nn.BatchNorm2d(out_planes),
            )

        # SE layers
        self.fc1 = nn.Conv2d(out_planes, out_planes//16, kernel_size=1)
        self.fc2 = nn.Conv2d(out_planes//16, out_planes, kernel_size=1)

    def forward(self, x):
        out = F.relu(self.bn1(self.conv1(x)))
        out = F.relu(self.bn2(self.conv2(out)))
        out = self.bn3(self.conv3(out))
        shortcut = self.shortcut(x) if self.stride == 1 else out
        # Squeeze-Excitation
        w = F.avg_pool2d(out, out.size(2))
        w = F.relu(self.fc1(w))
        w = self.fc2(w).sigmoid()
        out = out * w + shortcut
        return out

class EfficientNet(nn.Module):
    def __init__(self, device, cfg, num_classes=10):
        super(EfficientNet, self).__init__()
        self.device = device
        self.cfg = cfg
        self.conv1 = nn.Conv2d(3, 32, kernel_size=3,
                               stride=1, padding=1, bias=False)
        self.bn1 = nn.BatchNorm2d(32)
        self.layers = self._make_layers(in_planes=32)
        self.linear = nn.Linear(cfg[-1][1], num_classes)
        self.to(device)

    def _make_layers(self, in_planes):
        layers = []
        for expansion, out_planes, num_blocks, stride in self.cfg:
            strides = [stride] + [1]*(num_blocks-1)
            for stride in strides:
                layers.append(Block(in_planes, out_planes, expansion, stride))
                in_planes = out_planes
        return nn.Sequential(*layers)

    def forward(self, x,device):
        out = F.relu(self.bn1(self.conv1(x.to(device))))
        out = self.layers(out)
        out = out.view(out.size(0), -1)
        out = self.linear(out)
        return out
      
def EfficientNetB0():
    # (expansion, out_planes, num_blocks, stride)
    cfg = [(1,  16, 1, 2),
           (6,  24, 2, 1),
           (6,  40, 2, 2),
           (6,  80, 3, 2),
           (6, 112, 3, 1),
           (6, 192, 4, 2),
           (6, 320, 1, 2)]
    return EfficientNet(device,cfg)

net = EfficientNetB0()

In [0]:
criterion = nn.CrossEntropyLoss()


In [0]:
def train_epoch(train_loader, model, criterion, optimizer, scheduler, 
                epoch, device, log_interval, globaliter):

    # switch to train mode
    model.train()
    correct_train = 0

    # adjust_learning_rate
    if scheduler is not None:
        scheduler.step()

    for batch_idx, (input_data, target) in enumerate(train_loader):
      
        # TODO: do in other way (this is global batch index, for logging)
        globaliter += 1
      
        # extract batch data
        target = target.to(device)
        input_data = input_data.cuda()

        # compute output
        output = model(input_data,device)
        loss = criterion(output, target)
        
        #accuracy
        prediction = output.argmax(dim=1, keepdim=True)
        correct_train += prediction.eq(target.view_as(prediction)).sum().item()
        accuracy = 100. * correct_train / len(train_loader.dataset)

        # compute gradient and do optimizer step
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        # logging
        if batch_idx % log_interval == 0:
            print('Train Epoch: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}'.format(
                      epoch, batch_idx * len(input_data), len(train_loader.dataset),
                      100. * batch_idx / len(train_loader), loss.item()))
            # log loss
            writer_train.add_scalar('Train/RunningLoss', loss.item(), globaliter)
            # log LR
            lr = scheduler.get_lr()[0]
            writer_train.add_scalar('Train/LearningRate', lr, globaliter)
    print('\nTrain set: Accuracy: {}/{} ({:.0f}%)\n'.format(
           correct_train, len(train_loader.dataset), accuracy))    
    writer_train.add_scalar('Accuracy', accuracy, globaliter)
            
        

    return globaliter

In [0]:
def test_epoch(test_loader, model, criterion, 
                epoch, device, globaliter):
    
    #swatch to test mode
    model.eval()
    test_loss = 0
    correct = 0

    with torch.no_grad():
      for input_data, target in test_loader:
        data, target = input_data.to(device), target.to(device)
        predictions = model(input_data,device)

        #test_loss += criterion(predictions, target)
        prediction = predictions.argmax(dim=1, keepdim=True)
        correct += prediction.eq(target.view_as(prediction)).sum().item()

      #test_loss /= len(test_loader.dataset)
      accuracy = 100. * correct / len(test_loader.dataset)

      print('\nTest set:  Accuracy: {}/{} ({:.0f}%)\n'.format(
           correct, len(test_loader.dataset), accuracy))
      # log test_loss
      #writer_test.add_scalar('Test/RunningLoss', test_loss, globaliter)
      writer_test.add_scalar('Accuracy', accuracy, globaliter)

In [0]:
# path for dataset (will be not there after end of session)
current_time = str(datetime.datetime.now().timestamp())
path_log = 'logs/tensorboard/'

# set-up writer
writer_train = SummaryWriter(path_log+'/train/'+current_time+'/')
writer_test = SummaryWriter(path_log+'/test/'+current_time+'/')

writer_train = SummaryWriter(path_log+'/train/'+current_time+'/')
writer_test = SummaryWriter(path_log+'/test/'+current_time+'/')

In [26]:
ls logs/tensorboard/train/

1564920927.703416/  1564923057.833049/


In [47]:
%tensorboard --logdir logs/tensorboard/

Reusing TensorBoard on port 6006 (pid 3534), started 0:57:57 ago. (Use '!kill 3534' to kill it.)

In [46]:
# set number of epoch
n_epochs = 5

# set-up optimizer and scheduler
optimizer = torch.optim.SGD(net.parameters(), lr=0.001, momentum=0.9, weight_decay=5e-4)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer,
                                            step_size=50,
                                            gamma=0.1)

globaliter =0
print("Folder: ",current_time)
for epoch in range(1, n_epochs + 1):
    globaliter = train_epoch(trainloader, net, criterion, optimizer, scheduler, epoch, device, 200, globaliter)
    test_epoch(testloader, net, criterion, epoch, device, globaliter)

Train Epoch: 1 [0/50000 (0%)]	Loss: 2.328631
Train Epoch: 1 [6400/50000 (13%)]	Loss: 1.783298
Train Epoch: 1 [12800/50000 (26%)]	Loss: 1.496883
Train Epoch: 1 [19200/50000 (38%)]	Loss: 1.618731
Train Epoch: 1 [25600/50000 (51%)]	Loss: 1.563034
Train Epoch: 1 [32000/50000 (64%)]	Loss: 1.201609
Train Epoch: 1 [38400/50000 (77%)]	Loss: 1.560577
Train Epoch: 1 [44800/50000 (90%)]	Loss: 1.129387

Train set: Accuracy: 20088/50000 (40%)


Test set:  Accuracy: 5179/10000 (52%)

Train Epoch: 2 [0/50000 (0%)]	Loss: 1.224986
Train Epoch: 2 [6400/50000 (13%)]	Loss: 1.349765
Train Epoch: 2 [12800/50000 (26%)]	Loss: 1.183374
Train Epoch: 2 [19200/50000 (38%)]	Loss: 1.378267
Train Epoch: 2 [25600/50000 (51%)]	Loss: 1.190415
Train Epoch: 2 [32000/50000 (64%)]	Loss: 1.029423
Train Epoch: 2 [38400/50000 (77%)]	Loss: 1.089072
Train Epoch: 2 [44800/50000 (90%)]	Loss: 1.376410

Train set: Accuracy: 27203/50000 (54%)


Test set:  Accuracy: 5894/10000 (59%)

Train Epoch: 3 [0/50000 (0%)]	Loss: 0.875884
Train

In [50]:
# set number of epoch
n_epochs = 5

# set-up optimizer and scheduler
optimizer = torch.optim.SGD(net.parameters(), lr=0.1, momentum=0.9, weight_decay=5e-4)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer,
                                            step_size=50,
                                            gamma=0.1)

globaliter =0
for epoch in range(1, n_epochs + 1):
    globaliter = train_epoch(trainloader, net, criterion, optimizer, scheduler, epoch, device, 200, globaliter)
    test_epoch(testloader, net, criterion, epoch, device, globaliter)

Train Epoch: 1 [0/50000 (0%)]	Loss: 2.426053
Train Epoch: 1 [6400/50000 (13%)]	Loss: 2.170169
Train Epoch: 1 [12800/50000 (26%)]	Loss: 1.905327
Train Epoch: 1 [19200/50000 (38%)]	Loss: 1.551935
Train Epoch: 1 [25600/50000 (51%)]	Loss: 1.796376
Train Epoch: 1 [32000/50000 (64%)]	Loss: 1.291934
Train Epoch: 1 [38400/50000 (77%)]	Loss: 1.597436
Train Epoch: 1 [44800/50000 (90%)]	Loss: 1.917885

Train set: Accuracy: 17375/50000 (35%)


Test set:  Accuracy: 3810/10000 (38%)

Train Epoch: 2 [0/50000 (0%)]	Loss: 2.016333
Train Epoch: 2 [6400/50000 (13%)]	Loss: 1.334307
Train Epoch: 2 [12800/50000 (26%)]	Loss: 1.565201
Train Epoch: 2 [19200/50000 (38%)]	Loss: 1.627882
Train Epoch: 2 [25600/50000 (51%)]	Loss: 1.623110
Train Epoch: 2 [32000/50000 (64%)]	Loss: 1.490458
Train Epoch: 2 [38400/50000 (77%)]	Loss: 1.675368
Train Epoch: 2 [44800/50000 (90%)]	Loss: 1.529239

Train set: Accuracy: 22348/50000 (45%)


Test set:  Accuracy: 4200/10000 (42%)

Train Epoch: 3 [0/50000 (0%)]	Loss: 1.469719
Train